In [1]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
import IPython
from copy import copy
import os
from pathlib import Path
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

Генератор случайных данных

In [2]:
def get_random_k_choice_knapsack(m, n):
    B = np.random.randint(n*3, n*10)
    # предметы не влезающие в рюкзак сразу не берем
    A = np.random.randint(1, B, size=(m, n))
    C = np.random.randint(1, 10*B, size=(m, n))
    return A, C, B

A, C, B = get_random_k_choice_knapsack(3, 10)
A, C, B

(array([[22, 11, 16, 13,  5, 33, 27,  9,  4, 31],
        [ 4,  5, 19, 26, 27,  7, 27, 23, 20, 36],
        [ 5, 23, 15, 33,  5, 17, 26,  5, 27, 30]]),
 array([[ 93, 228, 243, 288, 377,  40, 196, 224,  80, 161],
        [337,  48, 245, 317, 361, 131, 332, 125, 182, 107],
        [176,   1, 117,  32, 353, 256, 233, 320, 302, 330]]),
 38)

In [3]:
def get_model(A, C, B):
    m = pyo.ConcreteModel()

    m.m, m.n = A.shape

    # на всякий случай, возьмем с собой
    m.A = A
    m.C = C
    m.B = B
    
    m.J = range(m.n)
    m.I = range(m.m)
    
    m.x = pyo.Var(m.J, domain=pyo.Binary)

    m.y = pyo.Var(m.I, m.J, domain=pyo.Binary)
    @m.Constraint(m.J)
    def для_каждой_колонки_выбираем_только_одну_строку(m, j):
        return sum(m.y[... ,j]) == m.x[j]

    m.f = pyo.Var(m.J, domain=pyo.NonNegativeIntegers)
    @m.Constraint(m.J)
    def конвертируем_выбор_в_номер(m, j):
        return sum(i * m.y[i ,j] for i in m.I) == m.f[j]

    m.obj = pyo.Objective(expr = sum( m.C[i, j] * m.y[i, j] for i in m.I for j in m.J), sense=pyo.maximize)

    @m.Constraint(m.I)
    def влезает_в_рюкзак(m, i):
        return sum(A[i, j] * m.y[i, j] for j in m.J) <= B

    return m

m = get_model(A, C, B)
m.pprint()

8 Set Declarations
    f_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   10 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   10 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9}
    y_index : Size=1, Index=None, Ordered=True
        Key  : Dimen : Domain              : Size : Members
        None :     2 : y_index_0*y_index_1 :   30 : {(0, 0), (0, 1), (0, 2), (0, 3), (0, 4), (0, 5), (0, 6), (0, 7), (0, 8), (0, 9), (1, 0), (1, 1), (1, 2), (1, 3), (1, 4), (1, 5), (1, 6), (1, 7), (1, 8), (1, 9), (2, 0), (2, 1), (2, 2), (2, 3), (2, 4), (2, 5), (2, 6), (2, 7), (2, 8), (2, 9)}
    y_index_0 : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    3 : {0, 1, 2}
    y_index_1 : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : 

In [4]:
solver = pyo.SolverFactory('cbc')
solver.solve(m).write()
m.x.extract_values(), m.f.extract_values()

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 2438.0
  Upper bound: 2438.0
  Number of objectives: 1
  Number of constraints: 13
  Number of variables: 30
  Number of binary variables: 40
  Number of integer variables: 50
  Number of nonzeros: 30
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.52
  Wallclock time: 0.29
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch and bou

({0: 1.0,
  1: 0.0,
  2: 1.0,
  3: 1.0,
  4: 1.0,
  5: 1.0,
  6: 1.0,
  7: 1.0,
  8: 1.0,
  9: 1.0},
 {0: 1.0,
  1: 0.0,
  2: 0.0,
  3: 0.0,
  4: 0.0,
  5: 1.0,
  6: 1.0,
  7: 2.0,
  8: 0.0,
  9: 2.0})